In [1]:

import itertools
import numpy as np
import os
import seaborn as sns
from tqdm import tqdm
from dataclasses import asdict, dataclass, field
import vsketch
import shapely.geometry as sg
from shapely.geometry import box, MultiLineString, Point, MultiPoint, Polygon, MultiPolygon, LineString
import shapely.affinity as sa
import shapely.ops as so
import matplotlib.pyplot as plt
import pandas as pd

import vpype_cli
from typing import List, Generic
from genpen import genpen as gp
from genpen.utils import Paper
from scipy import stats as ss
import geopandas
from shapely.errors import TopologicalError
import functools
import vpype
from skimage import io
from pathlib import Path

from sklearn.preprocessing import minmax_scale
from skimage import feature
from skimage import exposure

from skimage import filters
from skimage.color import rgb2gray
from skimage.transform import rescale, resize, downscale_local_mean
from skimage.morphology import disk
from pyaxidraw import axidraw   # import module

from PIL import Image

import fn
import cv2

from genpen.flow.field import *
from genpen.flow.particle import *
from genpen.genpen import random_line_subdivide_gen

import time

%load_ext autoreload
%autoreload 2

# more complex

In [2]:
image_path= '/home/naka/art/wigglesphere.jpg'
filename = 'qgrid_flowbeam.svg'
paper_size:str = '6x5.99 inches'
border:float=15  # mm
image_rescale_factor:float=0.04
smooth_disk_size:int=1
hist_clip_limit=0.1
hist_nbins=32
intensity_min=0.
intensity_max=1.
hatch_spacing_min=0.35  # mm
hatch_spacing_max=1.1 # mm
pixel_width=1 # mm
pixel_height=1 # mm
angle_jitter='ss.norm(loc=10, scale=0).rvs'  # degrees
pixel_rotation='0'  # degrees
merge_tolerances=[0.3, 0.4,]  # mm
simplify_tolerances=[0.2,]  # mm
savedir='/home/naka/art/plotter_svgs'

In [3]:
# make page
paper = Paper(paper_size)
drawbox = paper.get_drawbox(border)


In [4]:
x0gen = ss.uniform(loc=0.4, scale=0.3).rvs
x1gen = ss.uniform(loc=0.2, scale=0.1).rvs
split_func = functools.partial(gp.split_along_longest_side_of_min_rectangle, xgen=x0gen)
splits = gp.recursive_split_frac_buffer(
    drawbox, 
    split_func=split_func,
    p_continue=0.9, 
    depth=0, 
    depth_limit=10,
    buffer_frac=-0.0
)

bps = MultiPolygon([p for p in splits])

   
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.5mm')
sk.geometry(bps.boundary)

# tolerance=0.5

sk.display()

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-09-22T22:30:13.816065 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <polygon points="102.2168,234.6465 102.2168,234.6465 102.2168,234.6465 102.2168,234.6465 102.2168,234.6465 102.2168,234.6465 102.2168,234.6465 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.012,236.1399 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 101.0945,237.1107 104.0213,241.6598 108.9606,235.4932"/>
 
 
 
 
 
 <polygon points="122.8794,231.2703 122.8794,231.2703 122.8794,231.2703 122.8794,231.2703 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 123.4248,234.3412 129.8408,241.3031 131.8045,236.0311 131.8045,236.0311 131.8045,236.0311 123.2578,231.1004 123.2578,231.1004 123.2578,231.1004 123.2578,231.1004 123.2578,231.1004 123.2578,231.1004 123.2578,231.1004 123.2578,231.1004"/>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <polygon points="268.0669,200.6329 268.0669,200.6329 268.0669,200.6329 268.0669,200.6329 268.0669,200.6329 268.0669,200.6329 268.0669,200.6329 268.0669,200.6329 268.0669,200.6329 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 272.7504,201.6232 281.9985,198.6401 275.2122,191.2899 275.2122,191.2899 275.2122,191.2899 275.2122,191.2899 265.3516,196.6902 268.0669,200.6329"/>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <polygon points="211.6477,179.6845 211.6477,179.6845 211.6477,179.6845 211.6477,179.6845 211.6477,179.6845 217.3701,172.2611 217.3701,172.2611 217.3701,172.2611 212.2864,166.6098 212.2864,166.6098 212.2864,166.6098 212.2864,166.6098 198.4491,174.8198 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 206.7302,180.5389 211.6477,179.6845 211.6477,179.6845 211.6477,179.6845 211.6477,179.6845 211.6477,179.6845"/>
 
 
 
 
 
 <polygon points="176.0875,159.3762 176.0875,159.3762 180.7183,162.5744 180.7183,162.5744 180.7183,162.5744 180.7183,162.5744 180.7183,162.5744 180.7183,162.5744 180.7183,162.5744 180.7183,162.5744 180.7183,162.5744 186.6039,161.4936 186.6039,161.4936 186.6039,161.4936 186.6039,161.4936 186.6039,161.4936 186.6039,161.4936 186.6039,161.4936 186.6039,161.4936 186.6039,161.4936 193.8172,150.5683 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.1551,159.2353 176.0875,159.3762"/>
 
 
 
 
 
 
 
 
 
 
 
 <polygon points="204.4252,100.3161 204.4252,100.3161 204.4252,100.3161 186.4155,137.8511 186.4155,137.8511 186.4155,137.8511 186.4155,137.8511 186.4155,137.8511 188.5037,140.1725 188.5037,140.1725 188.5037,140.1725 188.5037,140.1725 188.5038,140.1725 188.5038,140.1725 188.5038,140.1725 188.5038,140.1725 188.5038,140.1725 228.8731,139.8693 205.1139,100.4772 205.1139,100.4772 205.1139,100.4772 205.1139,100.4772 205.1139,100.4772 205.1139,100.4772 205.1139,100.4772 205.1139,100.4772 205.1139,100.4772 204.4252,100.3161"/>
 <polygon points="234.7845,149.6702 234.7845,149.6702 234.7845,149.6702 234.7845,149.6702 228.8731,139.8693 228.8731,139.8693 228.8731,139.8693 228.8731,

In [5]:
all_bps = gp.Shape(bps)

In [6]:
# make pixel polys
prms = []
for bp in tqdm(bps):

#     a = np.random.uniform(0, 240)
    dist_from_center = bp.centroid.distance(bps.centroid)
    a = np.interp(dist_from_center, [0, 150], [0, 1020])
    prm = {
        'geometry':bp,
        'raw_pixel_width':pixel_width,
        'raw_pixel_height':pixel_height,
        'angle':a,
        'group': 'raw_hatch_pixel',
        'magnitude': np.random.uniform(0.3, 2),

    }
    prms.append(prm)
raw_hatch_pixels = geopandas.GeoDataFrame(prms)

100%|██████████| 696/696 [00:00<00:00, 3245.95it/s]


In [7]:
#  rescale polys to fit in drawbox
bbox = box(*raw_hatch_pixels.total_bounds)
_, transform = gp.make_like(bbox, drawbox, return_transform=True)
A = gp.AffineMatrix(**transform)
scaled_hatch_pixels = raw_hatch_pixels.copy()
scaled_hatch_pixels['geometry'] = scaled_hatch_pixels.affine_transform(A.A_flat)
scaled_hatch_pixels['scaled_pixel_height'] = scaled_hatch_pixels['geometry'].apply(gp.get_height)
scaled_hatch_pixels['scaled_pixel_width'] = scaled_hatch_pixels['geometry'].apply(gp.get_width)

In [8]:
new_drawbox = so.unary_union(scaled_hatch_pixels.geometry)
db = gp.Poly(new_drawbox)

In [9]:
# scaled_hatch_pixels['angle'] = np.interp(scaled_hatch_pixels.geometry.centroid.y, [db.bottom, db.top], [0, 680]) + np.random.randn(len(scaled_hatch_pixels)) * 5

In [10]:
scaled_hatch_pixels['angle'] = scaled_hatch_pixels['angle'] // 5 * 5

In [11]:
# scaled_hatch_pixels['angle'] = np.interp(scaled_hatch_pixels['angle'], xp=[0, 180], fp=[30, 150])

In [12]:
qpg = NoisyQuantizedPiecewiseGrid(scaled_hatch_pixels, xstep=5, ystep=5, noise_scale=0.1, noise_mult=0.5, verbose=False)
qpg.make_grid()

25it [00:00, 30.69it/s]


In [13]:
spiral_angle_max = np.pi * 40
spiral_angle_min = 0
spiral_angle_spacing = np.pi * 0.1001
sp_angle_range = np.arange(spiral_angle_min, spiral_angle_max, spiral_angle_spacing)
spiral_distances = np.linspace(0, 100, len(sp_angle_range))

start_points = [Point(np.cos(a) * d, np.sin(a) * d) for a, d in zip(sp_angle_range, spiral_distances)]

In [14]:
start_points = gp.make_like(MultiPoint(start_points), db.p)

In [15]:
poly = new_drawbox
pts = []
lss = []
n_steps = 19
for pt in tqdm(start_points):
    
    vp = VectorParticle(pos=pt, grid=qpg, stepsize=1, momentum_factor=np.random.uniform(0,0))
    for ii in range(n_steps):
        vp.step()
    if len(vp.pts) > 1:
        ls = gp.merge_LineStrings([LineString(vp.pts)])
    lss.append(ls)

 24%|██▍       | 98/400 [00:20<01:04,  4.67it/s]


KeyboardInterrupt: 

In [ ]:
buffer_gen = ss.uniform(loc=0.5, scale=0.5).rvs
d_buffer_gen = functools.partial(np.random.uniform, low=-0.35, high=-0.30)
d_translate_factor_gen = ss.uniform(loc=0.6, scale=0.8).rvs

In [ ]:
fills = []
all_polys = Polygon()
for ii, l in enumerate(tqdm(lss[:])):
    p = l.buffer(0.5, cap_style=2, join_style=2)
    p = p.buffer(buffer_gen(), cap_style=2, join_style=2)
    angles_gen = gp.make_callable(sp_angle_range[ii])
#     angles_gen = gp.make_callable(-90)
    stp = gp.ScaleTransPrms(d_buffer=d_buffer_gen(),angles=angles_gen(),d_translate_factor=d_translate_factor_gen(), n_iters=300)
    stp.d_buffers += np.random.uniform(-0.05, 0.05, size=stp.d_buffers.shape)
    P = gp.Poly(p)
    P.fill_scale_trans(**stp.prms)
    visible_area = p.difference(all_polys)
    visible_fill = P.fill.intersection(visible_area.buffer(1e-6))
    
    fills.append(visible_fill)
    all_polys = so.unary_union([all_polys, p])

In [ ]:
blss = gp.merge_LineStrings([f for f in fills if f.length > 0.1])


In [ ]:
blss = blss.intersection(drawbox)

In [ ]:
n_layers = 1

In [ ]:
layers = []
for ii in range(n_layers):
    fills = []
    for p in bps:
        xjitter_func = 0
        yjitter_func = ss.norm(loc=0, scale=np.random.uniform(0.1, 1.5)).rvs
        dist_from_center = bp.centroid.distance(bps.centroid)
        a = np.interp(dist_from_center, [0, 150], [0, 1020])
        bhf = gp.BezierHatchFill(
            spacing=np.random.uniform(0.4, 1.4),
            degrees=a,
            poly_to_fill=p, 
            xjitter_func=xjitter_func, 
            yjitter_func=yjitter_func,
            fill_inscribe_buffer=1.4,
            n_nodes_per_line=15,
            n_eval_points=100,
        )
        fills.append(bhf.p)

    fills = [f for f in fills if f.length > 0]
    layer = gp.merge_LineStrings(fills)
    layers.append(layer)

In [ ]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.3mm')
for i, layer in enumerate(layers):
    sk.stroke(i+1)
    sk.geometry(layer)

# sk.stroke(len(layers)+2)
# sk.geometry(blss)
    
sk.display(color_mode='layer')

In [ ]:
filename = '0002_qgrid_bhatch.svg'

In [ ]:
sk.vpype('linemerge -t 0.4 linesimplify linesort')

In [ ]:
savepath = Path(savedir).joinpath(filename).as_posix()
sk.save(savepath)

In [ ]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.stroke(1)
sk.geometry(blss)
    
sk.display()

# circle fluffs

In [16]:
image_path= '/home/naka/art/wigglesphere.jpg'
filename = 'qgrid_flowbeam.svg'
paper_size:str = '6x5.99 inches'
border:float=15  # mm
image_rescale_factor:float=0.04
smooth_disk_size:int=1
hist_clip_limit=0.1
hist_nbins=32
intensity_min=0.
intensity_max=1.
hatch_spacing_min=0.35  # mm
hatch_spacing_max=1.1 # mm
pixel_width=1 # mm
pixel_height=1 # mm
angle_jitter='ss.norm(loc=10, scale=0).rvs'  # degrees
pixel_rotation='0'  # degrees
merge_tolerances=[0.3, 0.4,]  # mm
simplify_tolerances=[0.2,]  # mm
savedir='/home/naka/art/plotter_svgs'

In [17]:
# make page
paper = Paper(paper_size)
drawbox = paper.get_drawbox(border)


In [18]:
bps = gp.circle_pack_within_poly(drawbox, rads=[20, 10, 5, 2.5])

 75%|███████▌  | 3/4 [00:00<00:00,  6.45it/s]

In [19]:
bps2 = gp.circle_pack_within_poly(drawbox, rads=[20, 10, 5,])


  0%|          | 0/3 [00:00<?, ?it/s]

In [20]:
bps = bps.difference(bps2.boundary.buffer(0.5))

In [21]:
n_layers = 1

In [22]:
layers = []
for ii in range(n_layers):
    fills = []
    for p in bps:
        xjitter_func = 0
        yjitter_func = ss.norm(loc=0, scale=np.random.uniform(0.1, 1.5)).rvs
        dist_from_center = p.centroid.distance(bps.centroid)
        a = np.interp(dist_from_center, [0, 150], [0, 1020])
        bhf = gp.BezierHatchFill(
            spacing=np.random.uniform(0.4, 1.4),
            degrees=a,
            poly_to_fill=p, 
            xjitter_func=xjitter_func, 
            yjitter_func=yjitter_func,
            fill_inscribe_buffer=1.4,
            n_nodes_per_line=15,
            n_eval_points=100,
        )
        fills.append(bhf.p)

    fills = [f for f in fills if f.length > 0]
    layer = gp.merge_LineStrings(fills)
    layers.append(layer)

 75%|███████▌  | 3/4 [00:08<00:02,  2.88s/it]


In [23]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.3mm')
for i, layer in enumerate(layers):
    sk.stroke(i+1)
    sk.geometry(layer)

# sk.stroke(len(layers)+2)
# sk.geometry(blss)
    
sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-09-22T22:30:54.811929 
 
 
 
 
 
 
 <polyline points="185.0928,66.4658 185.3053,66.6511 185.551,66.8655 185.7961,67.0801 186.0399,67.295 186.282,67.5104 186.5217,67.7263 186.7585,67.9429 186.9916,68.1605 187.2204,68.3791 187.4439,68.5991 187.6614,68.8205 187.872,69.0436 188.0747,69.2687 188.2686,69.496 188.4526,69.7258 188.6257,69.9582 188.7871,70.1935 188.9357,70.432 189.0707,70.6739 189.1913,70.9193 189.297,71.1684 189.3871,71.4214 189.4614,71.6784 189.5195,71.9393 189.5617,72.2041 189.588,72.4729 189.5989,72.7456 189.5951,73.0218 189.5774,73.3015 189.547,73.5844 189.505,73.8701 189.4532,74.1583 189.393,74.4485 189.3262,74.7404 189.255,75.0333 189.2364,75.1072"/>
 <polyline points="189.4288,75.2249 189.5179,74.9682 189.6217,74.6672 189.7223,74.3669 189.8173,74.0681 189.9044,73.7711 189.9817,73.4767 190.0473,73.1851 190.0997,72.8968 190.1377,72.612 190.1604,72.3311 190.167,72.0542 190.1571,71.7813 190.1307,71.5125 190.0877,71.2478 190.0285,70.9872 189.9536,70.7304 189.8637,70.4774 189.7597,70.2278 189.6426,69.9815 189.5134,69.7382 189.3733,69.4976 189.2235,69.2594 189.0653,69.0233 188.8999,68.7889 188.7286,68.5561 188.5526,68.3244 188.373,68.0935 188.1911,67.8633 188.0078,67.6334 187.8243,67.4035 187.6413,67.1735 187.4599,66.9432 187.2808,66.7123 187.1046,66.4806 186.932,66.248 186.7636,66.0144 186.5998,65.7797 186.4409,65.5437 186.2875,65.3064 186.1396,65.0678 185.9974,64.8277 185.8611,64.5861 185.7308,64.3431 185.6093,64.1044"/>
 <polyline points="187.6406,60.7809 187.6793,60.8318 187.8528,61.0641 188.0223,61.2974 188.1873,61.5319 188.3472,61.7676 188.5014,62.0047 188.6497,62.2432 188.7917,62.4834 188.9274,62.7251 189.0569,62.9683 189.1803,63.213 189.2981,63.4592 189.4105,63.7067 189.5182,63.9553 189.6218,64.2049 189.722,64.4554 189.8195,64.7066 189.9152,64.9582 190.0098,65.2101 190.104,65.4621 190.1987,65.7139 190.2945,65.9655 190.392,66.2167 190.4917,66.4673 190.594,66.7172 190.6992,66.9665 190.8074,67.215 190.9185,67.4628 191.0324,67.7099 191.1487,67.9564 191.2669,68.2025 191.3864,68.4482 191.5063,68.6938 191.6257,68.9395 191.7435,69.1856 191.8587,69.4324 191.9698,69.6802 192.0758,69.9293 192.1751,70.18 192.2667,70.4326 192.3492,70.6875 192.4214,70.9449 192.4824,71.2051 192.5311,71.4684 192.5669,71.7348 192.5891,72.0046 192.5975,72.2779 192.5919,72.5546 192.5724,72.8347 192.5395,73.1182 192.4938,73.4049 192.4362,73.6944 192.368,73.9867 192.2904,74.2812 192.2052,74.5777 192.114,74.8756 192.0189,75.1744 191.922,75.4738 191.8255,75.773 191.7317,76.0716 191.6714,76.2735"/>
 <polyline points="191.8575,76.3296 191.8681,76.3131 192.0913,75.9825 192.3232,75.6497 192.5607,75.3155 192.8004,74.9808 193.0389,74.6464 193.2727,74.3131 193.4986,73.9819 193.7133,73.6533 193.9137,73.3284 194.0969,73.0076 194.2604,72.6918 194.402,72.3814 194.5196,72.0769 194.6118,71.7788 194.6774,71.4872 194.7157,71.2024 194.7264,70.9244 194.7097,70.6532 194.666,70.3887 194.5961,70.1307 194.5014,69.8789 194.3833,69.6328 194.2437,69.3921 194.0846,69.1562 193.9083,68.9246 193.7171,68.6966 193.5137,68.4717 193.3006,68.2492 193.0805,68.0284 192.856,67.8087 192.6297,67.5895 192.404,67.3701 192.1814,67.1499 191.964,66.9284 191.7541,66.7051 191.5534,66.4795 191.3637,66.2512 191.1865,66.0198 191.0229,65.785 190.874,65.5466 190.7406,65.3043 190.6231,65.0581 190.5219,64.8079 190.437,64.5536 190.3682,64.2953 190.315,64.0332 190.2769,63.7673 190.253,63.4979 190.2421,63.2253 190.2432,62.9497 190.2546,62.6715 190.2749,62.3912 190.3023,62.1091 190.3348,61.8257 190.3703,61.5416 190.4066,61.2573 190.4414,60.9733 190.4719,60.6904 190.4955,60.4093 190.509,60.1306 190.509,59.8553 190.4917,59.5843 190.4527,59.3186 190.3869,59.0596 190.2908,58.8153"/>
 <polyline points="193.2677,57.9055 193.294,58.0639 193.3118,58.3348 193.3095,58.6107 193.2919,58.8904 193.2628,59.173 193.2255,59.4575 193.1828,59.7434 193.137,60.0301 193.0903,60.317 193.0443,60.6037 193.0008,60.8898 192.9612,61.1749 192.9266,61.4588 192.89

In [ ]:
filename = '0004_circle_bhatch.svg'

In [ ]:
sk.vpype('linemerge -t 0.4 linesimplify linesort')

In [ ]:
savepath = Path(savedir).joinpath(filename).as_posix()
sk.save(savepath)

# circle fluffs

In [24]:
image_path= '/home/naka/art/wigglesphere.jpg'

paper_size:str = '6x5.99 inches'
border:float=15  # mm
image_rescale_factor:float=0.04
smooth_disk_size:int=1
hist_clip_limit=0.1
hist_nbins=32
intensity_min=0.
intensity_max=1.
hatch_spacing_min=0.35  # mm
hatch_spacing_max=1.1 # mm
pixel_width=1 # mm
pixel_height=1 # mm
angle_jitter='ss.norm(loc=10, scale=0).rvs'  # degrees
pixel_rotation='0'  # degrees
merge_tolerances=[0.3, 0.4,]  # mm
simplify_tolerances=[0.2,]  # mm
savedir='/home/naka/art/plotter_svgs'

In [25]:
# make page
paper = Paper(paper_size)
drawbox = paper.get_drawbox(border)


In [26]:
bps = gp.circle_pack_within_poly(drawbox, rads=[20, 10, 5, 2.5])

 75%|███████▌  | 3/4 [00:00<00:00,  4.34it/s]

In [27]:
bps2 = gp.circle_pack_within_poly(drawbox, rads=[20, 10, 5,])


  0%|          | 0/3 [00:00<?, ?it/s]

In [28]:
bps = bps.difference(bps2.boundary.buffer(0.5))

In [29]:
n_layers = 1

In [30]:
layers = []
for ii in range(n_layers):
    fills = []
    for p in bps:
        xjitter_func = 0
        yjitter_func = ss.norm(loc=0, scale=np.random.uniform(0.1, 1.5)).rvs
        dist_from_center = p.centroid.distance(bps.centroid)
        a = np.interp(dist_from_center, [0, 150], [0, 1020])
        bhf = gp.BezierHatchFill(
            spacing=np.random.uniform(0.4, 1.4),
            degrees=a,
            poly_to_fill=p, 
            xjitter_func=xjitter_func, 
            yjitter_func=yjitter_func,
            fill_inscribe_buffer=1.4,
            n_nodes_per_line=15,
            n_eval_points=100,
        )
        fills.append(bhf.p)

    fills = [f for f in fills if f.length > 0]
    layer = gp.merge_LineStrings(fills)
    layers.append(layer)

 67%|██████▋   | 2/3 [00:00<00:00,  4.33it/s]


In [31]:
mlayers = [layer.buffer(0.001).buffer(-0.001).boundary for layer in layers]

In [32]:
mlayers = [gp.merge_LineStrings([l for l in layer if l.length > 0.2]) for layer in mlayers]

In [33]:
sns.displot([np.log10(l.length) for l in mlayers[0]])

In [34]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.3mm')
for i, layer in enumerate(mlayers):
    sk.stroke(i+1)
    sk.geometry(layer)

# sk.stroke(len(layers)+2)
# sk.geometry(blss)
    
sk.display(color_mode='layer')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-09-22T22:31:20.893860 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <polygon points="510.8518,340.4516 510.8786,340.4758 510.8788,340.476 510.9188,340.517 510.919,340.5172 510.9192,340.5175 510.9194,340.5179 510.9196,340.5182 510.9197,340.5186 510.9198,340.5189 510.9198,340.5193 510.9198,340.5197 510.9198,340.52 510.9198,340.5204 510.8367,340.9021 510.8367,340.9021 510.8367,340.9021 510.9187,340.5253 510.9188,340.5249 510.9189,340.5246 510.9191,340.5242 510.9193,340.5239 510.9195,340.5236 510.9198,340.5234 510.92,340.5231 510.9203,340.5229 510.9207,340.5227 510.921,340.5226 510.9213,340.5225 510.9217,340.5224 510.9221,340.5223 510.9224,340.5223 510.9228,340.5223 510.9232,340.5224 510.9235,340.5225 510.9239,340.5226 510.9242,340.5228 510.9245,340.523 510.9248,340.5232 510.9251,340.5234 511.0067,340.6071 510.9216,340.5199 510.9214,340.5196 510.9211,340.5193 510.921,340.519 510.9208,340.5186 510.9207,340.5183 510.9206,340.5179 510.9205,340.5175 510.9205,340.5172 510.9206,340.5168 510.9206,340.5164 510.9227,340.5071 510.9217,340.5116 510.9216,340.5119 510.9215,340.5123 510.9213,340.5126 510.9211,340.5129 510.9209,340.5132 510.9206,340.5135 510.9203,340.5137 510.92,340.5139 510.9197,340.5141 510.9194,340.5143 510.919,340.5144 510.9187,340.5145 510.9183,340.5145 510.9179,340.5145 510.9176,340.5145 510.9172,340.5144 510.9168,340.5144 510.9165,340.5142 510.9162,340.5141 510.9159,340.5139 510.9156,340.5136 510.9153,340.5134 510.8788,340.476 510.8787,340.4759"/>
 
 
 
 <polygon points="511.5917,336.2856 511.5845,336.1018 511.5845,336.1014 511.5845,336.1011 511.5846,336.1007 511.5847,336.1003 511.5849,336.1 511.585,336.0997 511.5852,336.0994 511.5855,336.0991 511.5858,336.0988 511.586,336.0986 511.5864,336.0984 511.5867,336.0982 511.587,336.0981 511.5874,336.098 511.5877,336.0979 511.5881,336.0979 511.5885,336.0979 511.5889,336.0979 511.5892,336.098 511.5896,336.0981 511.5899,336.0983 511.5902,336.0984 511.5905,336.0986 511.5908,336.0989 511.5911,336.0992 511.5913,336.0994 511.6729,336.2121 511.6731,336.2125 511.7394,336.3327 511.6731,336.2124 511.6729,336.2122 511.5847,336.0902 511.5845,336.0899 511.5843,336.0896 511.5842,336.0893 511.5841,336.0889 511.584,336.0885 511.584,336.0882 511.5777,335.9272 511.5777,335.9271 511.5777,335.927 511.5777,335.9273 511.5835,336.0768 511.5835,336.0772 511.5835,336.0776 511.5834,336.0779 511.5833,336.0783 511.5831,336.0786 511.583,336.079 511.5827,336.0793 511.5825,336.0795 511.5822,336.0798 511.582,336.08 511.5816,336.0802 511.5813,336.0804 511.581,336.0806 511.5806,336.0807 511.5802,336.0807 511.5799,336.0808 511.5795,336.0808 511.5791,336.0807 511.5788,336.0806 511.5784,336.0805 511.5781,336.0804 511.5778,336.0802 511.5774,336.08 511.5772,336.0798 511.5769,336.0795 511.5767,336.0792 511.514,335.9926 511.5139,335.9925 511.3323,335.7962 511.3322,335.796 511.3321,335.7959 511.3324,335.7962 511.5138,335.9924 511.5141,335.9927 511.5833,336.0884 511.5835,336.0887 511.5837,336.089 511.5838,336.0894 511.5839,336.0897 511.584,336.0901 511.584,336.0905"/>
 
 
 <polygon points="507.6951,330.6082 507.65,330.3841 507.65,330.3839 507.6038,330.0485 507.6037,330.0483 507.5917,329.9066 507.5917,329.9063 507.5917,329.9059 507.5918,329.9056 507.6419,329.6531 507.5969,329.8798 507.5968,329.8802 507.5967,329.8806 507.5965,329.8809 507.5963,329.8812 507.5961,329.8815 507.5959,329.8818 507.5956,329.882 507.5953,329.8823 507.595,329.8824 507.5946,329.8826 507.5943,329.8827 507.5939,329.8828 507.5936,329.8829 507.5932,329.8829 507.5928,329.8829 507.5924,329.8828 507.5921,329.8827 507.5917,329.8826 507.5914,329.8824 507.5911,329.8822 507.5908,329.882 507.5905,329.8817 507.5903,329.8815 507.59,329.8812 507.5898,329.8808 507.5897,329.8805 507.5896,329.8802 507.5895,329.8798 507.5894,329.8794 507.5805,329.7737 507.5917,329.9056 507.5

In [ ]:
filename = fn.Fn(postfix='-circle_bez_morsed.svg', git_sha_size=5, pid_sha_size=6).name(utc=False, milli=False)

In [ ]:
sk.vpype('splitall linemerge -t 0.1 linesimplify linemerge -t 0.3 linesimplify linemerge -t 0.5 linesimplify linesort')

In [ ]:
sk.display(color_mode='layer')

In [ ]:
savepath = Path(savedir).joinpath(filename).as_posix()
sk.save(savepath)

# particles?

In [ ]:
# make pixel polys
prms = []
for bp in tqdm(bps):

#     a = np.random.uniform(0, 240)
    dist_from_center = bp.centroid.distance(bps.centroid)
    a = np.interp(dist_from_center, [0, 150], [0, 1020])
    prm = {
        'geometry':bp,
        'raw_pixel_width':pixel_width,
        'raw_pixel_height':pixel_height,
        'angle':a,
        'group': 'raw_hatch_pixel',
        'magnitude': np.random.uniform(0.3, 2),

    }
    prms.append(prm)
raw_hatch_pixels = geopandas.GeoDataFrame(prms)

In [ ]:
#  rescale polys to fit in drawbox
bbox = box(*raw_hatch_pixels.total_bounds)
_, transform = gp.make_like(bbox, drawbox, return_transform=True)
A = gp.AffineMatrix(**transform)
scaled_hatch_pixels = raw_hatch_pixels.copy()
scaled_hatch_pixels['geometry'] = scaled_hatch_pixels.affine_transform(A.A_flat)
scaled_hatch_pixels['scaled_pixel_height'] = scaled_hatch_pixels['geometry'].apply(gp.get_height)
scaled_hatch_pixels['scaled_pixel_width'] = scaled_hatch_pixels['geometry'].apply(gp.get_width)

In [ ]:
new_drawbox = so.unary_union(scaled_hatch_pixels.geometry)
db = gp.Poly(new_drawbox)

In [ ]:
qpg = NoisyQuantizedPiecewiseGrid(scaled_hatch_pixels, xstep=5, ystep=5, noise_scale=0.1, noise_mult=1.5, verbose=False)
qpg.make_grid()

In [ ]:
start_points = []
for bp in scaled_hatch_pixels['geometry']:
    start_points += gp.get_random_points_in_polygon(bp, bp.area//4+5) 

In [ ]:
start_points = gp.make_like(MultiPoint(start_points), db.p)

In [ ]:
poly = new_drawbox
pts = []
lss = []
n_steps = 12
for pt in tqdm(start_points):
    
    vp = VectorParticle(pos=pt, grid=qpg, stepsize=1, momentum_factor=np.random.uniform(0,0))
    for ii in range(n_steps):
        vp.step()
    if len(vp.pts) > 1:
        ls = gp.merge_LineStrings([LineString(vp.pts)])
        lss.append(ls)

In [ ]:
lss = gp.merge_LineStrings([f for f in lss if f.length > 0.1])

In [ ]:
split_inds = np.array_split(np.arange(len(lss)), 1000)

In [ ]:
layers = []
for split_ind in split_inds:
    ls = gp.merge_LineStrings([lss[ii] for ii in split_ind])
    layers.append(ls)

In [ ]:
filename = fn.Fn(postfix='-circle_bez_morsed.svg', git_sha_size=5, pid_sha_size=6).name(utc=False, milli=False)

In [ ]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.3mm')
# sk.geometry(lss)
# sk.stroke(2)
# sk.geometry(bps.boundary)
for ii, l in enumerate(layers):
    sk.stroke(ii + 1)
    sk.geometry(l)
    
# sk.stroke(len(layers)+2)
# sk.geometry(blss)
    
sk.display(color_mode='layer')

In [ ]:
sk.vpype('splitall linemerge -t 0.1 linesimplify linemerge -t 0.2 linesort')

In [ ]:
sk.display(color_mode='layer')

In [ ]:
savepath = Path(savedir).joinpath(filename).as_posix()
sk.save(savepath)

In [ ]:
n_layers = 1

In [ ]:
sns.displot([p.centroid.distance(bps.centroid) for p in bps])

In [ ]:

fills = []
for p in bps:
    xjitter_func = 0
    yjitter_func = ss.norm(loc=0, scale=np.random.uniform(0.1, 1.5)).rvs
    dist_from_center = p.centroid.distance(bps.centroid)
    a = np.interp(dist_from_center, [0, 80], [0, 180])
    bhf = gp.BezierHatchFill(
        spacing=np.random.uniform(0.3, 0.9),
        degrees=a,
        poly_to_fill=p, 
        xjitter_func=xjitter_func, 
        yjitter_func=yjitter_func,
        fill_inscribe_buffer=1.4,
        n_nodes_per_line=15,
        n_eval_points=100,
    )
    fills.append(bhf.p)

fills = [f for f in fills if f.length > 0]
lss = gp.merge_LineStrings(fills)

In [ ]:
split_inds = np.array_split(np.arange(len(lss)), 1000)

In [ ]:
layers = []
for split_ind in split_inds:
    ls = gp.merge_LineStrings([lss[ii] for ii in split_ind])
    layers.append(ls)

In [ ]:
filename = fn.Fn(postfix='-circle_bez_morsed.svg', git_sha_size=5, pid_sha_size=6).name(utc=False, milli=False)

In [ ]:
sk = vsketch.Vsketch()
sk.size(paper.page_format_mm)
sk.scale('1mm')
sk.penWidth('0.3mm')
# sk.geometry(lss)
# sk.stroke(2)
# sk.geometry(bps.boundary)
for ii, l in enumerate(layers):
    sk.stroke(ii + 1)
    sk.geometry(l)
    
# sk.stroke(len(layers)+2)
# sk.geometry(blss)
    
sk.display(color_mode='layer')

In [ ]:
sk.vpype('splitall linemerge -t 0.1 linesimplify linemerge -t 0.2 linesort')

In [ ]:
sk.display(color_mode='layer')

In [ ]:
savepath = Path(savedir).joinpath(filename).as_posix()
sk.save(savepath)